# Extract Features

1. Read csv files and load as dfs
2. Combine dfs
3. Get POS, NER
4. Save in new features_df
5. Get semantic cosine similarity

In [1]:
import os, sys

import pandas as pd

# Get the current working directory of the notebook
notebook_dir = os.getcwd()
# Add the parent directory to the system path
sys.path.append(os.path.join(notebook_dir, '../'))

import log_files
from log_files import LogData
from data_processing import DataProcessing
from feature_extraction import SpacyFeatureExtraction

In [2]:
pd.set_option('max_colwidth', 800)
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [3]:
log_file_path = "data/prediction_logs"
predictions = True
df = log_files.read_data(notebook_dir, log_file_path, predictions)
df

Start logging batch
log_directory: /orange/ufdatastudios/dj.brinkley/predictions/prediction_correctness_experiments/../data/prediction_logs
save_batch_directory: /orange/ufdatastudios/dj.brinkley/predictions/prediction_correctness_experiments/../data/prediction_logs/batch_1-prediction
CSV to DF
Load saved csv: /orange/ufdatastudios/dj.brinkley/predictions/prediction_correctness_experiments/../data/prediction_logs/batch_1-prediction/batch_1-from_df.csv
save_batch_directory: /orange/ufdatastudios/dj.brinkley/predictions/prediction_correctness_experiments/../data/prediction_logs/batch_2-prediction
CSV to DF
Load saved csv: /orange/ufdatastudios/dj.brinkley/predictions/prediction_correctness_experiments/../data/prediction_logs/batch_2-prediction/batch_2-from_df.csv
save_batch_directory: /orange/ufdatastudios/dj.brinkley/predictions/prediction_correctness_experiments/../data/prediction_logs/batch_3-prediction
CSV to DF
Load saved csv: /orange/ufdatastudios/dj.brinkley/predictions/prediction

Base Sentence  \
0                                                                                                                                                    Detravious, a financial analyst forecasts that the stock price at Johnson & Johnson will likely decrease in 2027 Q2.   
1                                                                                                                                                            On August 21, 2024, Goldman Sachs speculates that the operating cash flow at Microsoft will likely increase.   
2                                                                                                                                                                       Morgan Stanley predicts that on September 15, 2025, the S&P 500 composite index will likely rise.   
3                                                                                                                                                                                        According to Apple, the projected revenue at Amazon will likely fall in Q4 2026.   
4                                                                                                                                                                                   In Q2 2025, Wells Fargo envisions that the U.S. dollar index will likely stay stable.   
5                                                                                                                                                                              The Dow Jones Industrial Average will likely rise in Q3 2027, according to JPMorgan Chase.   
6                                                                                                                               The World Health Organization forecasts that the obesity rates at urban health centers in the United States will likely decrease in 2027.   
7                                                                                                                      On August 15, 2026, the American Heart Association speculates that the average physical activity levels at U.S. high schools will likely increase.   
8                                                                                                                                                   Dr. John Lee predicts that on January 10, 2028, public engagement in preventative health screenings will likely rise.   
9                                                                                                       According to the Centers for Disease Control and Prevention, the average sugar consumption at public school cafeterias in California will likely fall in Q2 2027.   
10                                                                                                                                                         In September 2027, Professor Jane Smith envisions that national nutritional awareness will likely stay stable.   
11                                                                                                                     Physical activity levels among teenagers will likely rise in June 2027, according to the National Institute of Child Health and Human Development.   
12                                                                                                                                                  The economic growth rate in the finance sector will likely decrease in 2027, according to economist Dr. Sophia Patel.   
13                                                                                                                                               On August 21, 2024, the Brookings Institution speculates that voter turnout at battleground states will likely increase.   
14                                                                                                                                                                       Dr. Henry Lee predicts that on November 3, 2025,

In [ ]:
df.to_csv(index=False)
compression_opts = dict(method='zip',
                         archive_name='predictions-all_domains.csv')  
df.to_csv('predictions-all_domains.zip', index=False,
           compression=compression_opts)  

In [ ]:
df[66 : 67]

In [ ]:
df[2 : 3]

- issue: `obesity rate` is not being captures by POS or NER.

In [ ]:
only_predictions = DataProcessing.df_to_list(df, 'Base Sentence')
print(only_predictions)

sfe_class = SpacyFeatureExtraction(df, "Base Sentence")
word_leveL_disable_components = ["lemmatizer"]
word_level_pos_tags, word_level_pos_mappings, word_level_ner_entities, word_level_ner_mappings =  sfe_class.extract_features(data=only_predictions, disable_components=word_leveL_disable_components)
all_word_level_pos_df = DataProcessing.convert_to_df(word_level_pos_tags, mapping=word_level_pos_mappings)
all_word_level_ner_df = DataProcessing.convert_to_df(word_level_ner_entities, word_level_ner_mappings)
pred_pos_ner_features = [all_word_level_pos_df, all_word_level_ner_df]
pred_pos_ner_features_df = DataProcessing.concat_dfs(pred_pos_ner_features, axis=1, ignore_index=False)
pred_pos_ner_features_df.head()

## Observations

In [ ]:
log_file_path = "data/observation_logs"
predictions = False
observations_df = log_files.read_data(notebook_dir, log_file_path, predictions)
observations_df.head(7)

In [ ]:
only_observations = DataProcessing.df_to_list(observations_df, 'Base Sentence')
# print(only_observations)
word_level_pos_tags, word_level_pos_mappings, word_level_ner_entities, word_level_ner_mappings = sfe_class.extract_features(data=only_observations, disable_components=word_leveL_disable_components)
all_word_level_pos_df = DataProcessing.convert_to_df(word_level_pos_tags, mapping=word_level_pos_mappings)
all_word_level_ner_df = DataProcessing.convert_to_df(word_level_ner_entities, word_level_ner_mappings)
obs_pos_ner_features = [all_word_level_pos_df, all_word_level_ner_df]
obs_pos_ner_features_df = DataProcessing.concat_dfs(obs_pos_ner_features, axis=1, ignore_index=False)
obs_pos_ner_features_df.head(3)

## Both

- Create a knowledge graph
    - Nodes: words
    - Edges: connection to other words (same/diff sentence)
- Look at code from Graphbreeding project on 2019 Mac

In [ ]:
pred_sentence_features_df = DataProcessing.include_sentence_and_label(pred_pos_ner_features_df, df)
pred_sentence_features_df.head(3)
pred_profit_filt = (pred_pos_ner_features_df.NOUN_1.values == 'profit')
pred_profit_df = pred_pos_ner_features_df.loc[pred_profit_filt == True]
pred_profit_df

In [ ]:
pred_profit_sentences = DataProcessing.df_to_list(pred_profit_df, 'Base Sentence')
# pred_profit_sentences_2 = DataProcessing.df_to_list(pred_profit_df, 'Base Sentence')
# pred_profit_sentences_3 = DataProcessing.df_to_list(pred_profit_df, 'Base Sentence')
# pred_profit_sentences_4 = DataProcessing.df_to_list(pred_profit_df, 'Base Sentence')


In [ ]:
obs_profit_sentence_df = DataProcessing.include_sentence_and_label(obs_pos_ner_features_df, observations_df)
obs_profit_filt = (obs_pos_ner_features_df.NOUN_1.values == 'profit')
obs_profit_df = obs_pos_ner_features_df.loc[obs_profit_filt == True]
obs_profit_df

In [ ]:
obs_profit_sentences = DataProcessing.df_to_list(obs_profit_df, 'Base Sentence')
obs_profit_sentences

In [ ]:
pred_obs_dict = {}
for pred_sent_idx in range(len(pred_profit_sentences)):
    pred_sentence = pred_profit_sentences[pred_sent_idx]
    pred_obs_dict[pred_sentence] = obs_profit_sentences
pred_obs_dict

In [ ]:
import spacy

load_nlp_model = spacy.load("en_core_web_sm")

all_mappings = {} # Mapping of predictions to observations
pom_mappings = {} # Mapping of predictions to observations to metrics/scoresl pos can be misleading

oms = []
for prediction in pred_obs_dict.keys():
    print(f"Prediction: {prediction}")

    om_mappings = {} # Mapping of observations to metrics/scores

    for observation in pred_obs_dict[prediction]:
        print(f"    Observation: {observation}")

        # Calculate the similarity score
        prediction_doc = load_nlp_model(prediction)
        observation_doc = load_nlp_model(observation)
        similarity = prediction_doc.similarity(observation_doc)
        print(f"    Similarity: {similarity}")
        om_mappings[observation] = [similarity]
        print()   
        # print(f"    OM Mapping: {om_mappings}")
    pom_mappings[prediction] = om_mappings

# Flatten the dictionary into a list of rows
data = []
for prediction, observations in pom_mappings.items():
    for observation, scores in observations.items():
        data.append([prediction, observation, scores[0]])

# Create the DataFrame
df = pd.DataFrame(data, columns=['Prediction', 'Observation', 'Spacy Similarity'])

# Display the DataFrame
df['Scores'] = "Similarity"
df

In [ ]:
data

In [ ]:
table = pd.pivot_table(df, values='Spacy Similarity', index=['Prediction', 'Observation'],
                       columns=['Scores'])

- Only grouping by `p_a = profit`. 
- What if also group by sentiment?
    - fall/decrease ---  drastically different --- neutral bc dd doesn't indicate slope/how
    - fall --- plummeted, so similar

In [ ]:
table

In [ ]:
# Methods to alter Precision and Recall for prob rather than binary
    
#     https://en.wikipedia.org/wiki/Fuzzy_classification

# Support or deny classes

In [ ]:
from sentence_transformers import SentenceTransformer

# 1. Load a pretrained Sentence Transformer model
model = SentenceTransformer("all-MiniLM-L6-v2")

# The sentences to encode
sentences = [
    "The weather is lovely today.",
    "It's so sunny outside!",
    "He drove to the stadium.",
]

# 2. Calculate embeddings by calling model.encode()
embeddings = model.encode(sentences)
print(embeddings.shape)
# [3, 384]

# 3. Calculate the embedding similarities
similarities = model.similarity(embeddings, embeddings)
print(similarities)
# tensor([[1.0000, 0.6660, 0.1046],
#         [0.6660, 1.0000, 0.1411],
#         [0.1046, 0.1411, 1.0000]])

In [ ]:
pred_profit_sentences

In [ ]:
obs_profit_sentences

In [ ]:
my_sentences = pred_profit_sentences + obs_profit_sentences
my_sentences

In [ ]:
my_sentences = ["10%", "10.5", "11"]

In [ ]:
from sentence_transformers import SentenceTransformer

# 1. Load a pretrained Sentence Transformer model
model = SentenceTransformer("all-MiniLM-L6-v2")

# 2. Calculate embeddings by calling model.encode()
embeddings = model.encode(my_sentences)
print(embeddings.shape)
# [3, 384]

# 3. Calculate the embedding similarities
similarities = model.similarity(embeddings, embeddings)
print(similarities)
# tensor([[1.0000, 0.6660, 0.1046],
#         [0.6660, 1.0000, 0.1411],
#         [0.1046, 0.1411, 1.0000]])